# Yelp Data

## Introduction
* the website we get the data is: https://www.yelp.com/dataset/download
* The reason we can use the data is: https://s3-media3.fl.yelpcdn.com/assets/srv0/engineering_pages/bea5c1e92bf3/assets/vendor/yelp-dataset-agreement.pdf , and we use this data totally for academic reason.

## Data cleaning

First get the data

In [1]:
import pandas as pd
import ast
import datetime
import numpy as np
from fuzzywuzzy import fuzz
import re, string
from collections import Counter

c:\users\xinyi\appdata\local\programs\python\python37\lib\site-packages\fuzzywuzzy\fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


In [2]:
df_business=pd.read_json('./yelp-data/yelp_academic_dataset_business.json', lines=True)

In [3]:
# set the restaurant to be restaurant or food or coffee&tea
df_business['restaurant']=(df_business['categories'].str.contains("Restaurant"))
df_business['food']=(df_business['categories'].str.contains("Food"))
df_business['Coffee & Tea']=(df_business['categories'].str.contains("Coffee & Tea"))

In [4]:
df_business= df_business.loc[(df_business['restaurant'] == True) | (df_business['food'] == True) | (df_business['Coffee & Tea'] == True)]

In [5]:
df_business

business_id                        name  \
8       pQeaRpvuhoEqudo3uymHIQ         The Empanadas House   
12      M_guz7Dj7hX0evS672wIwA  Chocolate Shoppe Ice Cream   
20      CsLQLiRoafpJPJSkNX2h5Q            Middle East Deli   
23      mKTq1T_IAplDpHUcMzOXkw                  Tipsy Ryde   
24      eBEfgOPG7pvFhb2wcG9I7w             Philthy Phillys   
...                        ...                         ...   
209383  BAVuLTDmpSzDCk37A5HjtQ           Bruegger's Bagels   
209385  hskVqZCPqy-omm9CHi44xQ                    Domino's   
209388  9Q0fPWAjUweoFDk0kafuzQ                 Nishi Sushi   
209389  PotiAhtDMYMNsJCzV0oLAw                     Walmart   
209390  SYa2j1boLF8DcGVOYfHPcA                   Five Guys   

                                 address           city state postal_code  \
8                         404 E Green St      Champaign    IL       61820   
12                     2831 Parmenter St      Middleton    WI       53562   
20              4508 E Independence Blvd      Charlotte    NC       28205   
23                                             Gastonia    NC       28054   
24      15480 Bayview Avenue, unit D0110         Aurora    ON     L4G 7J1   
...                                  ...            ...   ...         ...   
209383                   27045 Lorain Rd  North Olmsted    OH       44070   
209385             6420 Rea Rd, Suite B1      Charlotte    NC       28226   
209388                  9750 Weston Road        Vaughan    ON     L4H 2P2   
209389               3240 Wilkinson Blvd      Charlotte    NC       28208   
209390           7014-590 E Camelback Rd     Scottsdale    AZ       85251   

         latitude   longitude  stars  review_count  is_open  \
8       40.110446  -88.233073    4.5             5        1   
12      43.105310  -89.510142    3.5             6        1   
20      35.194894  -80.767442    3.0             5        0   
23      35.252842  -81.152698    3.5             3        1   
24      44.010962  -79.448677    4.5             4        1   
...           ...         ...    ...           ...      ...   
209383  41.416568  -81.921396    3.0            13        0   
209385  35.078538  -80.818358    2.0            16        1   
209388  43.838555  -79.559823    4.0             5        0   
209389  35.226307  -80.893539    2.0            13        0   
209390  33.504062 -111.929431    3.5            97        1   

                                               attributes  \
8       {'RestaurantsAttire': 'u'casual'', 'Restaurant...   
12      {'BikeParking': 'True', 'Caters': 'True', 'Whe...   
20      {'RestaurantsGoodForGroups': 'True', 'OutdoorS...   
23                 {'BusinessAcceptsCreditCards': 'True'}   
24      {'RestaurantsTableService': 'False', 'Restaura...   
...                                                   ...   
209383  {'NoiseLevel': 'u'average'', 'BikeParking': 'F...   
209385  {'BusinessAcceptsCreditCards': 'True', 'Restau...   
209388  {'Ambience': '{'romantic': False, 'intimate': ...   
209389  {'RestaurantsPriceRange2': '1', 'BusinessParki...   
209390  {'BusinessAcceptsCreditCards': 'True', 'Restau...   

                                               categories  \
8       Ethnic Food, Food Trucks, Specialty Food, Impo...   
12              Desserts, Food, Ice Cream & Frozen Yogurt   
20             Food, Restaurants, Grocery, Middle Eastern   
23      Hotels & Travel, Transportation, Taxis, Beer, ...   
24                 Restaurants, Cheesesteaks, Poutineries   
...                                                   ...   
209383  Restaurants, Sandwiches, Food, Breakfast & Bru...   
209385  Restaurants, Pizza, Sandwiches, Fast Food, Chi...   
209388                  Japanese, Sushi Bars, Restaurants   
209389  Department Stores, Food, Mobile Phones, Fashio...   
209390  American (New), Food, Burgers, Restaurants, Fa...   

                                                    hours restaurant   food  \
8       {'Monday': '11:30-14:30', 'Tuesday': '1

For attributes column.

In [5]:
# get all the attributes of the business
attribute = []
for index, row in df_business.iterrows():
    current_attribute = row['attributes']
    if current_attribute == None:
        continue
    # print(current_attribute)
    current_attribute = current_attribute
    # print(current_attribute)
    for current_key in current_attribute.keys():
        if current_key not in attribute:
            # print(current_key)
            attribute.append(current_key)
    # print('----------')
attribute

['RestaurantsAttire',
 'RestaurantsTakeOut',
 'BusinessAcceptsCreditCards',
 'NoiseLevel',
 'GoodForKids',
 'RestaurantsReservations',
 'RestaurantsGoodForGroups',
 'BusinessParking',
 'RestaurantsPriceRange2',
 'HasTV',
 'Alcohol',
 'BikeParking',
 'RestaurantsDelivery',
 'ByAppointmentOnly',
 'OutdoorSeating',
 'Caters',
 'WheelchairAccessible',
 'WiFi',
 'RestaurantsTableService',
 'DogsAllowed',
 'Ambience',
 'GoodForMeal',
 'HappyHour',
 'BYOB',
 'Corkage',
 'DietaryRestrictions',
 'DriveThru',
 'BusinessAcceptsBitcoin',
 'AcceptsInsurance',
 'Music',
 'BestNights',
 'GoodForDancing',
 'Smoking',
 'BYOBCorkage',
 'CoatCheck',
 'AgesAllowed',
 'RestaurantsCounterService',
 'Open24Hours',
 'HairSpecializesIn']

In [6]:
# analyze each attribute:
for ananlyze_attr in attribute:
    ranges = []
    number = 0
    for index, row in df_business.iterrows():
        current_attribute = row['attributes']
        if current_attribute == None:
            continue
        if ananlyze_attr not in current_attribute.keys():
            continue
        current_val=current_attribute[ananlyze_attr]
        number = number + 1
        if current_val not in ranges:
            ranges.append(current_val)
    print(ananlyze_attr)
    print(number)
    print(ranges)
    print('-----------------------------------------------------')
    print('-----------------------------------------------------')

RestaurantsAttire
49348
["u'casual'", "'casual'", "u'formal'", "u'dressy'", 'None', "'dressy'", "'formal'"]
-----------------------------------------------------
-----------------------------------------------------
RestaurantsTakeOut
65956
['True', 'False', 'None']
-----------------------------------------------------
-----------------------------------------------------
BusinessAcceptsCreditCards
46141
['True', 'False', 'None']
-----------------------------------------------------
-----------------------------------------------------
NoiseLevel
43428
["u'quiet'", "u'average'", "u'loud'", "u'very_loud'", "'average'", "'quiet'", "'loud'", "'very_loud'", 'None']
-----------------------------------------------------
-----------------------------------------------------
GoodForKids
53207
['False', 'True', 'None']
-----------------------------------------------------
-----------------------------------------------------
RestaurantsReservations
53423
['False', 'True', 'None']
--------------

RestaurantsPriceRange2
68181
['1', '3', '2', '4', 'None']
-----------------------------------------------------
-----------------------------------------------------
HasTV
50009
['True', 'False', 'None']
-----------------------------------------------------
-----------------------------------------------------
Alcohol
47635
["'none'", "u'none'", "u'full_bar'", "u'beer_and_wine'", "'full_bar'", "'beer_and_wine'", 'None']
-----------------------------------------------------
-----------------------------------------------------
BikeParking
51910
['False', 'True', 'None']
-----------------------------------------------------
-----------------------------------------------------
RestaurantsDelivery
55618
['True', 'False', 'None']
-----------------------------------------------------
-----------------------------------------------------
ByAppointmentOnly
5174
['False', 'True', 'None']
-----------------------------------------------------
-----------------------------------------------------

GoodForMeal
35166
["{'dessert': False, 'latenight': False, 'lunch': False, 'dinner': False, 'brunch': False, 'breakfast': False}", "{'dessert': False, 'latenight': False, 'lunch': True, 'dinner': True, 'brunch': False, 'breakfast': False}", "{'dessert': False, 'latenight': False, 'lunch': False, 'dinner': False, 'brunch': True, 'breakfast': True}", "{'dessert': False, 'latenight': False, 'lunch': True, 'dinner': True, 'brunch': False, 'breakfast': True}", "{'dessert': False, 'latenight': False, 'lunch': True, 'dinner': False, 'brunch': True, 'breakfast': False}", "{'dessert': False, 'latenight': False, 'lunch': True, 'dinner': False, 'brunch': False, 'breakfast': False}", "{'dessert': False, 'latenight': False, 'lunch': False, 'dinner': True, 'brunch': False, 'breakfast': False}", "{'dessert': True, 'latenight': False, 'lunch': True, 'dinner': True, 'brunch': False, 'breakfast': False}", "{'dessert': None, 'latenight': None, 'lunch': True, 'dinner': True, 'brunch': None, 'breakfast': T

HappyHour
13581
['False', 'True', 'None']
-----------------------------------------------------
-----------------------------------------------------
BYOB
714
['False', 'True', 'None']
-----------------------------------------------------
-----------------------------------------------------
Corkage
1080
['False', 'True', 'None']
-----------------------------------------------------
-----------------------------------------------------
DietaryRestrictions
61
["{'dairy-free': False, 'gluten-free': False, 'vegan': False, 'kosher': False, 'halal': False, 'soy-free': False, 'vegetarian': True}", "{'dairy-free': False, 'gluten-free': False, 'vegan': True, 'kosher': False, 'halal': False, 'soy-free': False, 'vegetarian': False}", 'None', "{'dairy-free': False, 'gluten-free': True, 'vegan': False, 'kosher': False, 'halal': False, 'soy-free': False, 'vegetarian': False}", "{'dairy-free': False, 'gluten-free': True, 'vegan': False, 'kosher': False, 'halal': False, 'soy-free': False, 'vegetarian

BestNights
4370
["{'monday': False, 'tuesday': False, 'friday': False, 'wednesday': False, 'thursday': False, 'sunday': False, 'saturday': False}", "{'monday': False, 'tuesday': False, 'friday': True, 'wednesday': False, 'thursday': False, 'sunday': False, 'saturday': False}", "{'monday': False, 'tuesday': False, 'friday': True, 'wednesday': False, 'thursday': True, 'sunday': False, 'saturday': True}", "{'monday': True, 'tuesday': False, 'friday': True, 'wednesday': False, 'thursday': True, 'sunday': False, 'saturday': False}", "{'monday': False, 'tuesday': False, 'friday': True, 'wednesday': False, 'thursday': False, 'sunday': False, 'saturday': True}", "{'monday': False, 'tuesday': False, 'friday': False, 'wednesday': True, 'thursday': False, 'sunday': False, 'saturday': False}", "{'monday': True, 'tuesday': False, 'friday': False, 'wednesday': False, 'thursday': False, 'sunday': False, 'saturday': True}", "{'monday': True, 'tuesday': False, 'friday': False, 'wednesday': True, 'thurs

GoodForDancing
4079
['False', 'True', 'None']
-----------------------------------------------------
-----------------------------------------------------
Smoking
3167
["u'outdoor'", "u'no'", "u'yes'", "'no'", "'outdoor'", 'None', "'yes'"]
-----------------------------------------------------
-----------------------------------------------------
BYOBCorkage
1423
["'yes_free'", "'no'", "u'yes_corkage'", 'None', "'yes_corkage'", "u'yes_free'", "u'no'"]
-----------------------------------------------------
-----------------------------------------------------
CoatCheck
3742
['False', 'True', 'None']
-----------------------------------------------------
-----------------------------------------------------
AgesAllowed
41
["u'allages'", "u'21plus'", "u'19plus'", "u'18plus'", 'None']
-----------------------------------------------------
-----------------------------------------------------
RestaurantsCounterService
13
['True', 'False']
-----------------------------------------------------
---

In [7]:
# first for RestaurantsAttire, RestaurantsTakeOut, BusinessAcceptsCreditCards, NoiseLevel, GoodForKids, RestaurantsReservations, RestaurantsGoodForGroups, RestaurantsPriceRange2, HasTV, Alcohol, BikeParking, RestaurantsDelivery, ByAppointmentOnly, OutdoorSeating, Caters, WheelchairAccessible, WiFi, RestaurantsTableService, DogsAllowed, HappyHour. 
first_list_attribute = ['RestaurantsAttire', 'RestaurantsTakeOut', 'BusinessAcceptsCreditCards', 'NoiseLevel', 'GoodForKids', 'RestaurantsReservations', 'RestaurantsGoodForGroups', 'RestaurantsPriceRange2', 'HasTV', 'Alcohol', 'BikeParking', 'RestaurantsDelivery', 'ByAppointmentOnly', 'OutdoorSeating', 'Caters', 'WheelchairAccessible', 'WiFi', 'RestaurantsTableService', 'DogsAllowed', 'HappyHour']
for cur_attr in first_list_attribute:
    cur_list = []
    for index, row in df_business.iterrows():
        current_attribute = row['attributes']
        if current_attribute == None:
            cur_list.append('None')
            continue
        if cur_attr not in current_attribute.keys():
            cur_list.append('None')
            continue
        current_val=current_attribute[cur_attr]
        cur_list.append(current_val)
    df_business[cur_attr]=cur_list

In [8]:
# second for business parking:
parking_garage = []
parking_street = []
parking_validated = []
parking_lot = []
parking_valet = []
for index, row in df_business.iterrows():
        cur_attr = "BusinessParking"
        current_attribute = row['attributes']
        if current_attribute == None:
            parking_garage.append('None')
            parking_street.append('None')
            parking_validated.append('None')
            parking_lot.append('None')
            parking_valet.append('None')
            continue
        if cur_attr not in current_attribute.keys():
            parking_garage.append('None')
            parking_street.append('None')
            parking_validated.append('None')
            parking_lot.append('None')
            parking_valet.append('None')
            continue
        current_val=current_attribute[cur_attr]
        if current_val == 'None' or current_val == '{}':
            parking_garage.append('None')
            parking_street.append('None')
            parking_validated.append('None')
            parking_lot.append('None')
            parking_valet.append('None')
            continue
        else:
            #print(current_val)
            current_val = ast.literal_eval(current_val)
            if 'garage' in current_val.keys():
                parking_garage.append(current_val['garage'])
            else:
                parking_garage.append('None')
                
            if 'street' in current_val.keys():
                parking_street.append(current_val['street'])
            else:
                parking_street.append('None')
                
            if 'validated' in current_val.keys():
                parking_validated.append(current_val['validated'])
            else:
                parking_validated.append('None')
                
            if 'lot' in current_val.keys():
                parking_lot.append(current_val['lot'])
            else:
                parking_lot.append('None')
            
            if 'valet' in current_val.keys():
                parking_valet.append(current_val['valet'])
            else:
                parking_valet.append('None')
            

In [9]:
# add to the whole dataframe
df_business['parking_garage'] = parking_garage
df_business['parking_street'] = parking_street
df_business['parking_validated'] = parking_validated
df_business['parking_lot'] = parking_lot
df_business['parking_valet'] = parking_valet

In [10]:
# For Ambience:
total_word = {}
for index, row in df_business.iterrows():
        cur_attr = "Ambience"
        current_attribute = row['attributes']
        if current_attribute == None:
            continue
        if cur_attr not in current_attribute.keys():
            continue
        current_val=current_attribute[cur_attr]
        if current_val == 'None' or current_val == '{}':
            continue
        else:
            current_val = ast.literal_eval(current_val)
            for key in current_val.keys():
                if key in total_word:
                    total_word[key] = total_word[key] + 1
                else:
                    total_word[key] = 1
total_word
            

{'touristy': 49973,
 'hipster': 49417,
 'romantic': 49973,
 'intimate': 49973,
 'trendy': 49973,
 'upscale': 49804,
 'classy': 49973,
 'casual': 49973,
 'divey': 38864}

In [11]:
# gather these little attribute
# total_attri_l  = ['touristy', 'hipster','romantic', 'intimate', 'trendy', 'upscale', 'classy', 'casual', 'divey']
total_double_list = {'touristy':[], 'hipster':[],'romantic':[], 'intimate':[], 'trendy':[], 'upscale':[], 'classy':[], 'casual':[], 'divey':[]}
for index, row in df_business.iterrows():
        cur_attr = "Ambience"
        current_attribute = row['attributes']
        if current_attribute == None:
            for key in total_double_list.keys():
                total_double_list[key].append('None')
            continue
        if cur_attr not in current_attribute.keys():
            for key in total_double_list.keys():
                total_double_list[key].append('None')
            continue
        current_val=current_attribute[cur_attr]
        if current_val == 'None' or current_val == '{}':
            for key in total_double_list.keys():
                total_double_list[key].append('None')
            continue
        else:
            #print(current_val)
            current_val = ast.literal_eval(current_val)
            for key in total_double_list.keys():
                if key in current_val.keys():
                    total_double_list[key].append(current_val[key])
                else:
                    total_double_list[key].append('None')

In [12]:
# then add them
for key in total_double_list.keys():
    df_business[key] = total_double_list[key]

In [13]:
# and change the names:
df_business = df_business.rename(columns={'touristy':'Ambience_touristy', 'hipster': 'Ambience_hipster','romantic': 'Ambience_romantic', 'intimate': 'Ambience_intimate', 'trendy': 'Ambience_trendy', 'upscale': 'Ambience_upscale', 'classy': 'Ambience_classy', 'casual': 'Ambience_casual', 'divey': 'Ambience_divey'})

In [14]:
# Do the same thing for GoodForMeal:
total_word = {}
for index, row in df_business.iterrows():
        cur_attr = "GoodForMeal"
        current_attribute = row['attributes']
        if current_attribute == None:
            continue
        if cur_attr not in current_attribute.keys():
            continue
        current_val=current_attribute[cur_attr]
        if current_val == 'None' or current_val == '{}':
            continue
        else:
            current_val = ast.literal_eval(current_val)
            for key in current_val.keys():
                if key in total_word:
                    total_word[key] = total_word[key] + 1
                else:
                    total_word[key] = 1
total_word

{'dessert': 34688,
 'latenight': 34688,
 'lunch': 34688,
 'dinner': 34688,
 'brunch': 34690,
 'breakfast': 34688}

In [15]:
# gather these little attribute
# total_attri_l  = ['dessert', 'latenight','lunch', 'dinner', 'brunch', 'breakfast']
total_double_list = {'dessert': [], 'latenight': [],'lunch': [], 'dinner': [], 'brunch': [], 'breakfast': []}
for index, row in df_business.iterrows():
        cur_attr = "GoodForMeal"
        current_attribute = row['attributes']
        if current_attribute == None:
            for key in total_double_list.keys():
                total_double_list[key].append('None')
            continue
        if cur_attr not in current_attribute.keys():
            for key in total_double_list.keys():
                total_double_list[key].append('None')
            continue
        current_val=current_attribute[cur_attr]
        if current_val == 'None' or current_val == '{}':
            for key in total_double_list.keys():
                total_double_list[key].append('None')
            continue
        else:
            #print(current_val)
            current_val = ast.literal_eval(current_val)
            for key in total_double_list.keys():
                if key in current_val.keys():
                    total_double_list[key].append(current_val[key])
                else:
                    total_double_list[key].append('None')

In [16]:
# then add them
for key in total_double_list.keys():
    df_business[key] = total_double_list[key]

In [17]:
# and change the names:
df_business = df_business.rename(columns={'dessert':'GoodForMeal_dessert', 'latenight': 'GoodForMeal_latenight','lunch': 'GoodForMeal_lunch', 'dinner': 'GoodForMeal_dinner', 'brunch': 'GoodForMeal_brunch', 'breakfast': 'GoodForMeal_breakfast'})

In [18]:
# we don't need attributes this column any more:
df_business =df_business.drop(['attributes'], axis=1)

For categories column.

In [19]:
# get all the categories of the business
categories = []
for index, row in df_business.iterrows():
    current_attribute = row['categories']
    if current_attribute == None:
        continue
    # print(current_attribute)
    for current_key in current_attribute.split(", "):
        if current_key not in categories:
            # print(current_key)
            categories.append(current_key)
    # print('----------')
categories

['Ethnic Food',
 'Food Trucks',
 'Specialty Food',
 'Imported Food',
 'Argentine',
 'Food',
 'Restaurants',
 'Empanadas',
 'Desserts',
 'Ice Cream & Frozen Yogurt',
 'Grocery',
 'Middle Eastern',
 'Hotels & Travel',
 'Transportation',
 'Taxis',
 'Beer',
 'Wine & Spirits',
 'Food Delivery Services',
 'Cheesesteaks',
 'Poutineries',
 'Japanese',
 'Fast Food',
 'Food Court',
 'Shopping',
 'Organic Stores',
 'Health Markets',
 'Farmers Market',
 'Persian/Iranian',
 'Turkish',
 'Kebab',
 'Donuts',
 'Juice Bars & Smoothies',
 'Coffee & Tea',
 'Pretzels',
 'Bakeries',
 'Mexican',
 'Burgers',
 'Vietnamese',
 'Soup',
 'American (Traditional)',
 'Chicken Wings',
 'Lebanese',
 'American (New)',
 'Hot Dogs',
 'Chinese',
 'Shopping Centers',
 'Cafes',
 'Museums',
 'Local Flavor',
 'Flowers & Gifts',
 'Arts & Entertainment',
 'Art Galleries',
 'Florists',
 'Egyptian',
 'Pizza',
 'Buffets',
 'Indian',
 'Halal',
 'Breakfast & Brunch',
 'Salad',
 'Thai',
 'Sandwiches',
 'Italian',
 'Tapas/Small Plates'

In [20]:
# select the categories that we need:
categories_sum = {}
for cat in categories:
    categories_sum[cat] = 0
for index, row in df_business.iterrows():
    current_attribute = row['categories']
    if current_attribute == None:
        continue
    # print(current_attribute)
    for current_key in current_attribute.split(", "):
        categories_sum[current_key]  = categories_sum[current_key] + 1


In [21]:
categories_sum_1 = {}
for cat in categories:
    if categories_sum[cat] > 2000:
        categories_sum_1[cat] = categories_sum[cat]
categories_sum_1

{'Specialty Food': 5253,
 'Food': 32991,
 'Restaurants': 63944,
 'Desserts': 3824,
 'Ice Cream & Frozen Yogurt': 3034,
 'Grocery': 3862,
 'Beer': 2416,
 'Wine & Spirits': 2416,
 'Japanese': 2984,
 'Fast Food': 8106,
 'Shopping': 3382,
 'Juice Bars & Smoothies': 2017,
 'Coffee & Tea': 8415,
 'Bakeries': 4055,
 'Mexican': 5207,
 'Burgers': 6107,
 'American (Traditional)': 7596,
 'Chicken Wings': 3012,
 'American (New)': 5118,
 'Chinese': 4746,
 'Cafes': 3601,
 'Pizza': 7302,
 'Breakfast & Brunch': 6225,
 'Salad': 2988,
 'Sandwiches': 8064,
 'Italian': 5012,
 'Bars': 9490,
 'Nightlife': 9962,
 'Seafood': 2753,
 'Delis': 2079,
 'Event Planning & Services': 3651,
 'Caterers': 2451,
 'Sushi Bars': 2448,
 'Convenience Stores': 2117,
 'Sports Bars': 2009,
 'Asian Fusion': 2180,
 'Mediterranean': 2012}

In [22]:
# get the information of categories
categories = categories_sum_1
categories_column = {}
for cat in categories.keys():
    categories_column[cat] = []
for index, row in df_business.iterrows():
    current_attribute = row['categories']
    if current_attribute == None:
        for cat in categories_column.keys():
            categories_column[cat].append('None')
        continue
    cur_cat_list = current_attribute.split(", ")
    for cat in categories_column.keys():
        if cat not in cur_cat_list:
            categories_column[cat].append('False')
        else:
            categories_column[cat].append('True')


In [23]:
# then we add them to the dataframe
for cat in categories_column.keys():
    df_business["categories_{}".format(cat)] = categories_column[cat]

In [24]:
# seems we don't need the column food, coffee&tea, restaurant and categories anymore:
df_business =df_business.drop(['food', 'restaurant', 'Coffee & Tea', 'categories'], axis=1)

For checkin column:

In [25]:
# first, let's get the chekin information:
df_checkIn=pd.read_json('./yelp-data/yelp_academic_dataset_checkin.json', lines=True)

In [26]:
# first get all the checkIn since the business register on yelp.
result = []
for index, row in df_checkIn.iterrows():
    result.append(int((len(row['date'])+2)/21))

In [27]:
df_checkIn['total_checkIn'] = result

In [28]:
# for the chekIn happened in year 2019:
# let's first merge into the business dataframe:
df_business = pd.merge(df_business, df_checkIn, how='left', on=['business_id'])

In [29]:
# get the information of the new column
threshold = datetime.datetime.strptime("2019-01-01 19:53:31", '%Y-%m-%d %H:%M:%S').date()
checkIn_2019 = []
for index, row in df_business.iterrows():
    current_attribute = row['date']
    if current_attribute == None or current_attribute == 'NaN' or type(current_attribute) == float:
        checkIn_2019.append('None')
        continue
    cur_num = 0
    # print(current_attribute)
    # print('-----------')
    for time in current_attribute.split(", "):
        cur_time = datetime.datetime.strptime(time, '%Y-%m-%d %H:%M:%S').date()
        if cur_time >= threshold:
            cur_num = cur_num + 1
    checkIn_2019.append(cur_num)
checkIn_2019

[0,
 5,
 0,
 'None',
 1,
 0,
 0,
 2,
 13,
 0,
 2,
 0,
 0,
 13,
 0,
 0,
 0,
 1,
 0,
 3,
 0,
 4,
 0,
 0,
 2,
 5,
 'None',
 11,
 0,
 2,
 0,
 3,
 0,
 0,
 0,
 17,
 0,
 0,
 1,
 7,
 174,
 11,
 0,
 3,
 12,
 1,
 0,
 0,
 0,
 0,
 10,
 1,
 37,
 1,
 0,
 0,
 0,
 7,
 6,
 8,
 0,
 34,
 67,
 1,
 0,
 13,
 0,
 30,
 2,
 1,
 1,
 79,
 0,
 5,
 0,
 10,
 0,
 18,
 0,
 0,
 0,
 34,
 0,
 2,
 0,
 0,
 'None',
 0,
 2,
 0,
 5,
 61,
 11,
 4,
 161,
 10,
 0,
 0,
 6,
 0,
 0,
 0,
 0,
 0,
 9,
 0,
 0,
 0,
 2,
 1,
 0,
 0,
 0,
 0,
 1,
 8,
 20,
 29,
 1,
 215,
 2,
 0,
 77,
 0,
 3,
 1,
 11,
 2,
 12,
 0,
 'None',
 16,
 0,
 38,
 4,
 1,
 0,
 2,
 2,
 0,
 0,
 0,
 0,
 0,
 0,
 6,
 2,
 1,
 1,
 4,
 0,
 1,
 0,
 0,
 1,
 0,
 0,
 27,
 0,
 293,
 0,
 40,
 1,
 16,
 14,
 9,
 34,
 57,
 4,
 1,
 3,
 7,
 229,
 4,
 37,
 1,
 0,
 27,
 0,
 27,
 1,
 0,
 17,
 0,
 3,
 10,
 7,
 0,
 0,
 14,
 10,
 0,
 24,
 0,
 1,
 22,
 0,
 8,
 0,
 2,
 0,
 0,
 13,
 7,
 0,
 25,
 7,
 1,
 2,
 3,
 0,
 0,
 2,
 0,
 58,
 20,
 1,
 11,
 3,
 7,
 0,
 34,
 0,
 9,
 7,
 0,
 0,
 0,
 1,
 17,
 0

In [30]:
df_business['checkIn_2019'] = checkIn_2019

In [31]:
# we don't need date anymore
df_business =df_business.drop(['date'], axis=1)

looking for chain.

In [32]:
# Here we define chain to be store with 2 or more repeated names.
# chain = []
# for index, row in df_business.iterrows():
#     yesOrNot = 0
#     for index_2, row_2 in df_business.iterrows():
#         if row_2['business_id'] == row['business_id']:
#             continue
#         if fuzz.ratio(row['name'], row_2['name'])>80:
#             yesOrNot = 1
#             break
#     if yesOrNot == 1:
#         chain.append('True')
#     else:
#         chain.append('False')
# I found this program will run so so so so much time.....so oops!

In [50]:
# Hence, I then define chain to be store that have same name no matter upper or lower letter, no matter the punctuation, and here we go!
name = df_business['name']
def refresh(x):
    # get the lower case and left the punctuation
    dirty_string = x.lower()
    return re.sub(rf"[{string.punctuation}]", "", dirty_string)
name = name.apply(refresh)
name

0               the empanadas house
1        chocolate shoppe ice cream
2                  middle east deli
3                        tipsy ryde
4                   philthy phillys
                    ...            
80500              brueggers bagels
80501                       dominos
80502                   nishi sushi
80503                       walmart
80504                     five guys
Name: name, Length: 80505, dtype: object

In [55]:
# and we get the duplicate name:
select_name = [item for item, count in Counter(name).items() if count > 1]
select_name

['chocolate shoppe ice cream',
 'philthy phillys',
 'wetzels pretzels',
 'carls jr',
 'gourmet burger company',
 'meat chix and wieners',
 'amir',
 'amandos bros',
 'starbucks',
 'boomers sweet home chicago',
 'wendys',
 'china gourmet',
 'five guys burgers and fries',
 'the market by longos',
 'taco bell',
 'the pub',
 'nickels',
 'pizzaville',
 'petes fish  chips',
 'sugar bowl',
 'tim hortons',
 'marcos pizza',
 'dennys restaurant',
 'fromagerie des nations',
 'chilis grill  bar',
 'chicknjoy',
 'blimpie',
 'wine rack',
 'the keg steakhouse  bar',
 'lcbo',
 'walgreens',
 'st louis bar  grill',
 'pizza fresh',
 'dutch bros coffee',
 'menchies frozen yogurt',
 'veggie house',
 'mihito sushi laboratory',
 'kfc',
 'churchs chicken',
 'bp',
 'merry anns diner',
 'kings',
 'mcdonalds',
 'tropical smoothie cafe',
 'uswirl',
 'garcias',
 'liquor world',
 'jcs grill house',
 'fruits and roots',
 'bibab express',
 'chipotle mexican grill',
 'fat bastard burrito',
 'dunkin',
 'jasons deli',
 '

In [62]:
# And we add the chain column to the business dataframe
chain = []
for index, row in df_business.iterrows():
    cur_name = row['name']
    cur_name_new = refresh(cur_name)
    if cur_name_new in select_name:
          chain.append('True')
    else:
        chain.append('False')

In [63]:
df_business['chain'] = chain

How many cases has been discovered in the city where the restaurant locates?

In [83]:
# First as the require of the model, we don't need the restaurant that is closed.....so drop them!
df_business = df_business.loc[(df_business['is_open'] == 1)]

In [85]:
# Hence, we don't need this column
df_business =df_business.drop(['is_open'], axis=1)

In [372]:
# let's first get the case in the city.......quite hard, I am not sure whether this is consistent with the information 
# we have or not as they are all county or region name....not sure if they are same as city name ...
# The data I used is the folloiwng: https://github.com/nytimes/covid-19-data , 
# https://github.com/ishaberry/Covid19Canada, and the date I picked is 6/6 and 6/7 respectively..hoping they are accurate...
# Let's begin:
df_us_county = pd.read_csv("./us-counties.csv")

In [373]:
# let's first get the latest information
# since there is duplicate city name in different state, we have to first change the state name to abbreviation......sad!!!
df_us_state_abbr = pd.read_html("http://bigdave44.com/features/the-mine/us-states-abbreviations-capitals-nicknames/")[0]
df_us_state_abbr.columns = ['state','abbrv', 'capital', 'nickname']
df_us_state_abbr =df_us_state_abbr.drop(['capital', 'nickname'], axis=1)

In [374]:
df_us_county = pd.merge(df_us_county, df_us_state_abbr, how='left', on=['state'])
df_us_county

date      county       state     fips  cases  deaths abbrv
0       2020-01-21   Snohomish  Washington  53061.0      1       0    WA
1       2020-01-22   Snohomish  Washington  53061.0      1       0    WA
2       2020-01-23   Snohomish  Washington  53061.0      1       0    WA
3       2020-01-24        Cook    Illinois  17031.0      1       0    IL
4       2020-01-24   Snohomish  Washington  53061.0      1       0    WA
...            ...         ...         ...      ...    ...     ...   ...
212601  2020-06-06  Sweetwater     Wyoming  56037.0     32       0    WY
212602  2020-06-06       Teton     Wyoming  56039.0    100       1    WY
212603  2020-06-06       Uinta     Wyoming  56041.0     19       0    WY
212604  2020-06-06    Washakie     Wyoming  56043.0     38       3    WY
212605  2020-06-06      Weston     Wyoming  56045.0      1       0    WY

[212606 rows x 7 columns]

In [232]:
# df_us_county =df_us_county.drop(['fips'], axis=1)

In [233]:
# now we can continue to get the latest data...oho!
us_latest_case = {}
us_latest_death = {}
for index, row in df_us_county.iterrows():
    cur_tuple = (refresh(row['county']), row['abbrv'])
    us_latest_case[cur_tuple] = row['cases']
    us_latest_death[cur_tuple] = row['deaths']

In [234]:
# And for canada:
df_ca_region_case = pd.read_csv("./cases_timeseries_hr.csv")
df_ca_region_death = pd.read_csv("./mortality_timeseries_hr.csv")

In [235]:
df_ca_state_abbr = pd.read_html("https://www150.statcan.gc.ca/n1/pub/92-195-x/2011001/geo/prov/tbl/tbl8-eng.htm")[0]
df_ca_state_abbr.columns = ['province','noUse1', 'abbrv', 'noUse2','noUse3']
df_ca_state_abbr =df_ca_state_abbr.drop(['noUse1', 'noUse2','noUse3'], axis=1)

In [236]:
# change name in the province of df_ca_region_xx as there is some abbr in it
df_ca_region_case.loc[df_ca_region_case['province'] == 'BC', 'province'] = 'British Columbia'
df_ca_region_case.loc[df_ca_region_case['province'] == 'NL', 'province'] = 'Newfoundland and Labrador'
df_ca_region_case.loc[df_ca_region_case['province'] == 'NWT', 'province'] = 'Northwest Territories'
df_ca_region_case.loc[df_ca_region_case['province'] == 'PEI', 'province'] = 'Prince Edward Island'

In [237]:
df_ca_region_case = pd.merge(df_ca_region_case, df_ca_state_abbr, how='left', on=['province'])
df_ca_region_death = pd.merge(df_ca_region_death, df_ca_state_abbr, how='left', on=['province'])

In [238]:
latest_case = us_latest_case
latest_death = us_latest_death
for index, row in df_ca_region_case.iterrows():
    cur_tuple = (refresh(row['health_region']), row['abbrv'])
    latest_case[cur_tuple] = row['cumulative_cases']
for index, row in df_ca_region_death.iterrows():
    cur_tuple = (refresh(row['health_region']), row['abbrv'])
    latest_death[cur_tuple] = row['cumulative_deaths']


In [239]:
for key in latest_death.keys():
    if key not in latest_case.keys():
        latest_case[key] = 0
for key in latest_case.keys():
    if key not in latest_death.keys():
        latest_death[key] = 0

Let's first get the cumulative case/death in different state/province as it is too hard to get the health region information.

In [240]:
latest_case_state = {}
latest_death_state = {}
for key in latest_case.keys():
    cur_state = key[1]
    if cur_state in latest_case_state.keys():
        latest_case_state[cur_state] = latest_case_state[cur_state] + latest_case[key]
    else:
        latest_case_state[cur_state] = latest_case[key]
for key in latest_death.keys():
    cur_state = key[1]
    if cur_state in latest_death_state.keys():
        latest_death_state[cur_state] = latest_death_state[cur_state] + latest_death[key]
    else:
        latest_death_state[cur_state] = latest_death[key]

In [253]:
# And we add this to the dataset
covid_cumul_case_state = []
covid_cumul_death_state = []
# num = 0
# state_not_include = []
for index, row in df_business.iterrows():
    cur_state = row['state']
    if cur_state in latest_case_state.keys():
        covid_cumul_case_state.append(latest_case_state[cur_state])
        continue
    else:
        covid_cumul_case_state.append('None')
        # num = num + 1
        # state_not_include.append(row['state'])
        # print(row['city'])
# print(num)
# set(state_not_include)

for index, row in df_business.iterrows():
    cur_state = row['state']
    if cur_state in latest_death_state.keys():
        covid_cumul_death_state.append(latest_death_state[cur_state])
        continue
    else:
        covid_cumul_death_state.append('None')

In [257]:
df_business['covid_cumul_case_state'] = covid_cumul_case_state
df_business['covid_cumul_death_state'] = covid_cumul_death_state

Ok, let's find if we can merge all the canada's cities to the health region:

In [301]:
set(df_ca_region_case.loc[(df_ca_region_case['abbrv'] == "SK")]['health_region'])

0        False
1        False
2        False
3        False
4        False
         ...  
12820    False
12821    False
12822    False
12823    False
12824    False
Name: abbrv, Length: 12825, dtype: bool

In [201]:
# df_ca_postal_place = pd.read_csv("./ca_postal_codes.csv")
# num = 0
# summ = 0
# for area in list(set(df_ca_postal_place['Place Name'])):
#     summ = summ + 1
#     if area not in set(df_ca_region_case['health_region']):
#         #print(area)
#         num = num + 1
# print(num)
# print(summ)
# print(len(list(set(df_ca_region_case['health_region']))))

In [258]:
# # And we finally finally finally come to the df_business dataframe:
# covid_cumul_case = []
# covid_cumul_death = []
# num = 0
# city = []
# for index, row in df_business.iterrows():
#     cur_city = refresh(row['city'])
#     cur_tuple = (cur_city, row['state'])
#     if cur_tuple in latest_case.keys():
#         # covid_cumul_case.append(latest_case[cur_tuple])
#         continue
#     else:
#         #covid_cumul_case.append(0)
#         if row['state'] in set(df_us_state_abbr['abbrv']):
#             num = num + 1
#             city.append(row['city'])
# print(num)
# set(city)

It's 3:42 and I wanna to sleep, so I leave this and handeling later....

Let's try to get when the restaurant first established.

In [277]:
# First, let's get checkin information again
df_checkIn=pd.read_json('./yelp-data/yelp_academic_dataset_checkin.json', lines=True)

In [278]:
df_business = pd.merge(df_business, df_checkIn, how='left', on=['business_id'])

In [281]:
threshold = datetime.datetime.strptime("2020-06-09 19:53:31", '%Y-%m-%d %H:%M:%S').date()
dayOfStart = []
for index, row in df_business.iterrows():
    current_attribute = row['date']
    if current_attribute == None or current_attribute == 'NaN' or type(current_attribute) == float:
        dayOfStart.append('None')
        continue
    
    time = current_attribute.split(", ")[0]
    cur_time = datetime.datetime.strptime(time, '%Y-%m-%d %H:%M:%S').date()
    dayOfStart.append((threshold-cur_time).days)

In [283]:
df_business['dayOfStart'] = dayOfStart

In [285]:
df_business =df_business.drop(['date'], axis=1)

And what about the land price?

In [306]:
# for canada:
# so the data is from https://www150.statcan.gc.ca/t1/tbl1/en/tv.action?pid=3210004701 and I will use handwrite since there is no table found
# ca_land_price = [['NL', 5088], ['PE', 3802], ['NS', 2253], ['NB', 2403], ['QC', 6606], ['ON', 11225], ['MB', 2193], ['SK', 1489], ['AB', 2941], ['BC', 6451]]  what am I doing???
df_ca_land_price = pd.DataFrame([['NL', 'PE','NS','NB','QC','ON','MB','SK', 'AB','BC'],[5088, 3802, 2253, 2403, 6606, 11225, 2193, 1489, 2941, 6451]]).T

In [353]:
df_ca_land_price.columns = ['abbrv', 'price']

In [350]:
# for u.s.:
# the data is from https://downloads.usda.library.cornell.edu/usda-esmis/files/pn89d6567/g732dn07g/9306t9701/land0819.pdf
df_us_land_price = pd.read_excel('land0819.xlsx') 
df_us_land_price = pd.merge(df_us_land_price, df_us_state_abbr, how='left', on=['state'])
df_us_land_price = df_us_land_price.drop(['state'], axis=1)

In [356]:
land_price_dict = {}
for index, row in df_ca_land_price.iterrows():
    land_price_dict[row['abbrv']] = row['price']
for index, row in df_us_land_price.iterrows():
    land_price_dict[row['abbrv']] = row['price']

In [362]:
land_price = []
# num =0
for index, row in df_business.iterrows():
    cur_state = row['state']
    if cur_state in land_price_dict.keys():
        land_price.append(land_price_dict[cur_state])
    else:
        # num = num + 1
        # print(cur_state)
        # print(row['city'])
        land_price.append('None')

In [363]:
df_business['land_price'] = land_price #million dollar

Overlook:

In [394]:
df_business.to_csv('./total_business.csv', index=False)

File sent to vincent:

In [365]:
# df_tmp = df_business.loc[df_business['state'].isin(set(df_us_state_abbr['abbrv']))][['business_id', 'latitude', 'longitude']]
# df_tmp.to_csv('./tmp_business.csv', index=False)

In [423]:
# df_us_county = pd.read_csv("./us-counties.csv")
# df_us_county = df_us_county.dropna()

In [424]:
# df_us_state_abbr = pd.read_html("http://bigdave44.com/features/the-mine/us-states-abbreviations-capitals-nicknames/")[0]
# df_us_state_abbr.columns = ['state','abbrv', 'capital', 'nickname']
# df_us_state_abbr =df_us_state_abbr.drop(['capital', 'nickname'], axis=1)

In [425]:
# df_us_county = pd.merge(df_us_county, df_us_state_abbr, how='left', on=['state'])

In [426]:
# df_us_county.loc[(df_us_county['county'] == 'Unknown')]

Empty DataFrame
Columns: [date, county, state, fips, cases, deaths, abbrv]
Index: []

In [427]:
# us_latest_case_county = {}
# us_latest_death_county = {}
# for index, row in df_us_county.iterrows():
#     print(row['date'])
#     cur_tuple = (row['county'], row['abbrv'], row['fips'])
#     us_latest_case_county[cur_tuple] = row['cases']
#     us_latest_death_county[cur_tuple] = row['deaths']


2020-01-21
2020-01-22
2020-01-23
2020-01-24
2020-01-24
2020-01-25
2020-01-25
2020-01-25
2020-01-26
2020-01-26
2020-01-26
2020-01-26
2020-01-26
2020-01-27
2020-01-27
2020-01-27
2020-01-27
2020-01-27
2020-01-28
2020-01-28
2020-01-28
2020-01-28
2020-01-28
2020-01-29
2020-01-29
2020-01-29
2020-01-29
2020-01-29
2020-01-30
2020-01-30
2020-01-30
2020-01-30
2020-01-30
2020-01-31
2020-01-31
2020-01-31
2020-01-31
2020-01-31
2020-01-31
2020-02-01
2020-02-01
2020-02-01
2020-02-01
2020-02-01
2020-02-01
2020-02-01
2020-02-02
2020-02-02
2020-02-02
2020-02-02
2020-02-02
2020-02-02
2020-02-02
2020-02-02
2020-02-03
2020-02-03
2020-02-03
2020-02-03
2020-02-03
2020-02-03
2020-02-03
2020-02-03
2020-02-04
2020-02-04
2020-02-04
2020-02-04
2020-02-04
2020-02-04
2020-02-04
2020-02-04
2020-02-05
2020-02-05
2020-02-05
2020-02-05
2020-02-05
2020-02-05
2020-02-05
2020-02-05
2020-02-05
2020-02-06
2020-02-06
2020-02-06
2020-02-06
2020-02-06
2020-02-06
2020-02-06
2020-02-06
2020-02-06
2020-02-07
2020-02-07
2020-02-07

2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-08
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09
2020-03-09

2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13
2020-03-13

2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15
2020-03-15

2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17
2020-03-17

...

2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05

2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05
2020-06-05

2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06

2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06

2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06
2020-06-06

In [428]:
# for key in us_latest_death_county.keys():
#     if key not in us_latest_case_county.keys():
#         us_latest_case_county[key] = 0
# for key in us_latest_case_county.keys():
#     if key not in us_latest_death_county.keys():
#         us_latest_death_county[key] = 0
set(us_latest_death_county.keys()) == set(us_latest_case_county.keys())

True

In [429]:
#case = pd.DataFrame(list(us_latest_case_county), columns=['county','state','fips']).assign(case=us_latest_case_county.values())

In [430]:
#death = pd.DataFrame(list(us_latest_death_county), columns=['county','state','fips']).assign(death=us_latest_death_county.values())

In [432]:
#pd.merge(case, death, on=['county', 'state', 'fips']).to_csv('./us_total_county.csv', index=False)

In [411]:
#us_latest_death_county

{('Snohomish', 'WA', 53061.0): 152,
 ('Cook', 'IL', 17031.0): 3913,
 ('Orange', 'CA', 6059.0): 176,
 ('Maricopa', 'AZ', 4013.0): 489,
 ('Los Angeles', 'CA', 6037.0): 2620,
 ('Santa Clara', 'CA', 6085.0): 145,
 ('Suffolk', 'MA', 25025.0): 923,
 ('San Francisco', 'CA', 6075.0): 43,
 ('Dane', 'WI', 55025.0): 29,
 ('San Diego', 'CA', 6073.0): 312,
 ('Bexar', 'TX', 48029.0): 78,
 ('Douglas', 'NE', 31055.0): 47,
 ('Humboldt', 'CA', 6023.0): 4,
 ('Sacramento', 'CA', 6067.0): 59,
 ('Solano', 'CA', 6095.0): 23,
 ('Spokane', 'WA', 53063.0): 35,
 ('Salt Lake', 'UT', 49035.0): 81,
 ('Marin', 'CA', 6041.0): 17,
 ('Napa', 'CA', 6055.0): 3,
 ('Sonoma', 'CA', 6097.0): 4,
 ('Washington', 'OR', 41067.0): 18,
 ('King', 'WA', 53033.0): 578,
 ('Alameda', 'CA', 6001.0): 104,
 ('Hillsborough', 'FL', 12057.0): 90,
 ('Manatee', 'FL', 12081.0): 105,
 ('New York City', 'NY', nan): 0,
 ('Unknown', 'RI', nan): 0,
 ('Placer', 'CA', 6061.0): 9,
 ('San Mateo', 'CA', 6081.0): 88,
 ('Fulton', 'GA', 13121.0): 252,
 ('No

In [296]:
#pd.DataFrame(set(df_ca_region_case['health_region']))

0
0                        Interior
1                            Peel
2                  Simcoe Muskoka
3   Gaspésie-Îles-de-la-Madeleine
4                       Côte-Nord
..                            ...
81                          South
82                   Peterborough
83       Zone 4 (Edmundston area)
84       Zone 2 (Saint John area)
85                            NWT

[86 rows x 1 columns]

Generate the data of toronto:

In [36]:
df_bs_toronto = df_business.loc[df_business['city'].isin(['Toronto', 'Tornto', 'toronto'])]
df_bs_toronto = df_bs_toronto[['name', 'address', 'latitude', 'longitude', 'business_id']]
df_bs_toronto

name                     address  \
6                         Front Door Organics           415 Horner Avenue   
12                     Gourmet Burger Company          843 Kipling Avenue   
25                           Mi Mi Restaurant        688 Gerrard Street E   
32                      The Market by Longo's              100 Bloor St E   
41                                Tim Hortons        90 Adelaide Street W   
...                                       ...                         ...   
80475                        Get & Go Burrito  1077 Wilson Avenue, Unit 8   
80481                  Grasshopper Restaurant          310 College Street   
80490                            Q's Shawarma      1075 Martin Grove Road   
80495                               Starbucks           81 Front Street E   
80497  Steak & Cheese & Quick Pita Restaurant              199 College St   

        latitude  longitude             business_id  
6      43.603232 -79.538424  007Dg4ESDVacWcC4Vq704Q  
12     43.633291 -79.531768  rVBPQdeayMYht4Uv_FOLHg  
25     43.666376 -79.348773  0QjROMVW9ACKjhSEfHqNCQ  
32     43.670936 -79.384643  GtQPbazps0jt7_cJghfmsA  
41     43.649859 -79.382060  8k62wYhDVq1-652YbJi5eg  
...          ...        ...                     ...  
80475  43.726656 -79.480365  eUi3O-8Gqh_nJ_ZhO-25gQ  
80481  43.657716 -79.402098  yFQCdWr_k1pTObzHPGis9Q  
80490  43.701807 -79.575135  GAgEoHcf4PSuZRS5Zd3ltA  
80495  43.648727 -79.372506  BtTCTHwoIfr3fBQjaOkpIw  
80497  43.658683 -79.395071  n2BKYb8aw4AhRKLkdUjQRg  

[10993 rows x 5 columns]

In [37]:
df_bs_toronto.to_csv('./toronto_business.csv', index=False)

Generate the whole data:

In [38]:
df_bs_total = df_business_open[['name', 'address', 'latitude', 'longitude', 'business_id']]
df_bs_total.to_csv('./total_business.csv', index=False)

For great toronto area:

In [39]:
# from the website, we get the cities
url = 'https://en.wikipedia.org/wiki/List_of_municipalities_in_the_Greater_Toronto_Area'
df_gta = pd.read_html(url, header=0)
cities = df_gta[0]  # select table of cities
cities=list(cities['Census subdivision'])

In [40]:
# Use fuzzywuzzy to get the city name that will be include in the dataframe
result = []
for ci in cities:
    for i in df_business['city']:
        if fuzz.ratio(i, ci)>80:
            result.append(i)
result = set(result)

In [41]:
# finally get the new dataframe
df_business_gta = df_business.loc[df_business['city'].isin(result)]
df_business_gta

business_id                                    name  \
4      eBEfgOPG7pvFhb2wcG9I7w                         Philthy Phillys   
6      007Dg4ESDVacWcC4Vq704Q                     Front Door Organics   
7      9sRGfSVEfLhN_km60YruTA                      Apadana Restaurant   
12     rVBPQdeayMYht4Uv_FOLHg                  Gourmet Burger Company   
25     0QjROMVW9ACKjhSEfHqNCQ                        Mi Mi Restaurant   
...                       ...                                     ...   
80481  yFQCdWr_k1pTObzHPGis9Q                  Grasshopper Restaurant   
80490  GAgEoHcf4PSuZRS5Zd3ltA                            Q's Shawarma   
80495  BtTCTHwoIfr3fBQjaOkpIw                               Starbucks   
80497  n2BKYb8aw4AhRKLkdUjQRg  Steak & Cheese & Quick Pita Restaurant   
80502  9Q0fPWAjUweoFDk0kafuzQ                             Nishi Sushi   

                                address           city state postal_code  \
4      15480 Bayview Avenue, unit D0110         Aurora    ON     L4G 7J1   
6                     415 Horner Avenue        Toronto    ON     M8W 4W3   
7                    13071 Yonge Street  Richmond Hill    ON     L4E 1A5   
12                   843 Kipling Avenue        Toronto    ON     M8Z 5G9   
25                 688 Gerrard Street E        Toronto    ON     M4M 1Y3   
...                                 ...            ...   ...         ...   
80481                310 College Street        Toronto    ON     M5T 1S2   
80490            1075 Martin Grove Road        Toronto    ON     M9W 4W6   
80495                 81 Front Street E        Toronto    ON     M5E 1B8   
80497                    199 College St        Toronto    ON     M5T 1P9   
80502                  9750 Weston Road        Vaughan    ON     L4H 2P2   

        latitude  longitude  stars  review_count  ...  categories_Delis  \
4      44.010962 -79.448677    4.5             4  ...             False   
6      43.603232 -79.538424    4.0             8  ...             False   
7      43.947011 -79.454862    3.0             3  ...             False   
12     43.633291 -79.531768    3.0            13  ...             False   
25     43.666376 -79.348773    4.0           116  ...             False   
...          ...        ...    ...           ...  ...               ...   
80481  43.657716 -79.402098    4.0           177  ...             False   
80490  43.701807 -79.575135    4.0            16  ...             False   
80495  43.648727 -79.372506    4.0            22  ...             False   
80497  43.658683 -79.395071    2.5            21  ...             False   
80502  43.838555 -79.559823    4.0             5  ...             False   

      categories_Event Planning & Services categories_Caterers  \
4                                    False               False   
6                                    False               False   
7                                    False               False   
12                                   False               False   
25                                   False               False   
...                                    ...                 ...   
80481                                False               False   
80490                                False               False   
80495                                False               False   
80497                                False               False   
80502                                False               False   

      categories_Sushi Bars categories_Convenience Stores  \
4                     False                         False   
6                     False                         False   
7                     False                         False   
12                    False                         False   
25                    False                         False   
...                     ...                           ...   
80481                 False                         False   
80490                 False                   

Inquiry:

In [303]:
df_business.loc[(df_business['state'] == "SK")]

Empty DataFrame
Columns: [business_id, name, address, city, state, postal_code, latitude, longitude, stars, review_count, hours, RestaurantsAttire, RestaurantsTakeOut, BusinessAcceptsCreditCards, NoiseLevel, GoodForKids, RestaurantsReservations, RestaurantsGoodForGroups, RestaurantsPriceRange2, HasTV, Alcohol, BikeParking, RestaurantsDelivery, ByAppointmentOnly, OutdoorSeating, Caters, WheelchairAccessible, WiFi, RestaurantsTableService, DogsAllowed, HappyHour, parking_garage, parking_street, parking_validated, parking_lot, parking_valet, Ambience_touristy, Ambience_hipster, Ambience_romantic, Ambience_intimate, Ambience_trendy, Ambience_upscale, Ambience_classy, Ambience_casual, Ambience_divey, GoodForMeal_dessert, GoodForMeal_latenight, GoodForMeal_lunch, GoodForMeal_dinner, GoodForMeal_brunch, GoodForMeal_breakfast, categories_Specialty Food, categories_Food, categories_Restaurants, categories_Desserts, categories_Ice Cream & Frozen Yogurt, categories_Grocery, categories_Beer, categories_Wine & Spirits, categories_Japanese, categories_Fast Food, categories_Shopping, categories_Juice Bars & Smoothies, categories_Coffee & Tea, categories_Bakeries, categories_Mexican, categories_Burgers, categories_American (Traditional), categories_Chicken Wings, categories_American (New), categories_Chinese, categories_Cafes, categories_Pizza, categories_Breakfast & Brunch, categories_Salad, categories_Sandwiches, categories_Italian, categories_Bars, categories_Nightlife, categories_Seafood, categories_Delis, categories_Event Planning & Services, categories_Caterers, categories_Sushi Bars, categories_Convenience Stores, categories_Sports Bars, categories_Asian Fusion, categories_Mediterranean, total_checkIn, checkIn_2019, chain, covid_cumul_case_state, covid_cumul_death_state, dayOfStart]
Index: []

[0 rows x 94 columns]